## Part 2:  Use the Geocoder package or the csv file to create a dataframe using the geographical coordinates of each postal code


#### Reloaded previous data frame (from Question 1)

In [16]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

In [17]:
website_url = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

In [18]:
soup = BeautifulSoup(website_url, 'lxml')

In [19]:
My_table = soup.find('table',{'class':'wikitable sortable'})
My_table

<table class="wikitable sortable">
<tbody><tr>
<th>Postcode</th>
<th>Borough</th>
<th>Neighbourhood
</th></tr>
<tr>
<td>M1A</td>
<td>Not assigned</td>
<td>Not assigned
</td></tr>
<tr>
<td>M2A</td>
<td>Not assigned</td>
<td>Not assigned
</td></tr>
<tr>
<td>M3A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
</td></tr>
<tr>
<td>M4A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
</td></tr>
<tr>
<td>M5A</td>
<td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
<td><a href="/wiki/Harbourfront_(Toronto)" title="Harbourfront (Toronto)">Harbourfront</a>
</td></tr>
<tr>
<td>M5A</td>
<td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
<td><a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a>
</td></tr>
<tr>
<td>M6A</td>

In [20]:
table1=""
for tr in My_table.find_all('tr'):
    row1=""
    for tds in tr.find_all('td'):
        row1=row1+","+tds.text
    table1=table1+row1[1:]

In [21]:
headers="Postcode,Borough,Neighbourhood"
table_rows = My_table.find_all('tr')

res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        res.append(row)
df = pd.DataFrame(res, columns=["Postcode", "Borough", "Neighbourhood"])
df=df.rename(columns = {'Postcode':'Postal Code', 'Neighbourhood':'Neighborhood'})
df.head(10)

Postal Code           Borough      Neighborhood
0         M1A      Not assigned      Not assigned
1         M2A      Not assigned      Not assigned
2         M3A        North York         Parkwoods
3         M4A        North York  Victoria Village
4         M5A  Downtown Toronto      Harbourfront
5         M5A  Downtown Toronto       Regent Park
6         M6A        North York  Lawrence Heights
7         M6A        North York    Lawrence Manor
8         M7A      Queen's Park      Not assigned
9         M8A      Not assigned      Not assigned

In [22]:
indexNames = df[ df['Borough'] =='Not assigned'].index

df.drop(indexNames , inplace=True)

In [23]:
df.head(10)

Postal Code           Borough      Neighborhood
2          M3A        North York         Parkwoods
3          M4A        North York  Victoria Village
4          M5A  Downtown Toronto      Harbourfront
5          M5A  Downtown Toronto       Regent Park
6          M6A        North York  Lawrence Heights
7          M6A        North York    Lawrence Manor
8          M7A      Queen's Park      Not assigned
10         M9A         Etobicoke  Islington Avenue
11         M1B       Scarborough             Rouge
12         M1B       Scarborough           Malvern

In [24]:
result = df.groupby(['Postal Code','Borough'], sort=False).agg( ', '.join)

df_new=result.reset_index()
df_new.head(15)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A      Queen's Park   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   

                                         Neighborhood  
0                                           Parkwoods  
1                                    Victoria Village  
2                           Harbourfront, Regent Park  
3                    Lawrence Heights, Lawrence Manor  
4                                        Not assigned  
5                                    Islington Avenue  
6                                      Rouge, Malvern  
7                                     Don Mills North  
8                     Woodbine Gardens, Parkview Hill  
9                            Ryerson, Garden District  
10                                          Glencairn  
11  Cloverdale, Islington, Martin Grove, Princess ...  
12             Highland Creek, Rouge Hill, Port Union  
13                   Flemingdon Park, Don Mills South  
14                                   Woodbine Heights

In [25]:
df_new.shape

(103, 3)

# PART TWO BEGINS HERE

### Loaded csv file to create dataframe with latitude and longitude coordinates

In [26]:
!wget -q -O 'Toronto_long_lat_data.csv'  http://cocl.us/Geospatial_data
df_lon_lat = pd.read_csv('Toronto_long_lat_data.csv')
df_lon_lat.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [29]:
df_lon_lat.columns=['Postal Code','Latitude','Longitude']

In [30]:
df_lon_lat.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [31]:
Toronto_df = pd.merge(df_new,
                 df_lon_lat[['Postal Code','Latitude', 'Longitude']],
                 on='Postal Code')
Toronto_df

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A      Queen's Park   
5           M9A         Etobicoke   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
52          M2M        North York   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
95          M1X       Scarborough   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656

## PART THREE:  Explore and cluster the neighborhoods in Toronto

### Download all of the dependencies

In [32]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


### Explore and cluster Toronto neighborhoods

In [33]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="Toronto")
location = geolocator.geocode(address)
latitude_toronto = location.latitude
longitude_toronto = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude_toronto, longitude_toronto))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [35]:
map_toronto = folium.Map(location=[latitude_toronto, longitude_toronto], zoom_start=10)

# add markers to map
for lat, lng, borough, Neighborhood in zip(Toronto_df['Latitude'], Toronto_df['Longitude'], Toronto_df['Borough'], Toronto_df['Neighborhood']):
    label = '{}, {}'.format(Neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [40]:
CLIENT_ID = 'K3RJR0KS13UE0SPFOOACI3XMLU3EXO35GLODIPJMEPGK2JPV' # your Foursquare ID
CLIENT_SECRET = '2DNCRAR5Y03W323U3D554NIKL2UOIE3TIIEMSKFU3SQN2Q3F' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30

In [41]:
radius=200
LIMIT=50

In [44]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [45]:
toronto_venues = getNearbyVenues(names=Toronto_df['Neighborhood'],
                                   latitudes=Toronto_df['Latitude'],
                                   longitudes=Toronto_df['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront, Regent Park
Lawrence Heights, Lawrence Manor
Not assigned
Islington Avenue
Rouge, Malvern
Don Mills North
Woodbine Gardens, Parkview Hill
Ryerson, Garden District
Glencairn
Cloverdale, Islington, Martin Grove, Princess Gardens, West Deane Park
Highland Creek, Rouge Hill, Port Union
Flemingdon Park, Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens, Eringate, Markland Wood, Old Burnhamthorpe
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Downsview North, Wilson Heights
Thorncliffe Park
Adelaide, King, Richmond
Dovercourt Village, Dufferin
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto
Harbourfront East, Toronto Islands, Union Station
Little Portugal, Trinity
East Birchmount Park, Ionview, Kennedy Park
Bayview Village
CFB Toronto, Downsview East
The D

In [47]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                               50   
Agincourt                                                               4   
Agincourt North, L'Amoreaux East, Milliken, Ste...                      2   
Albion Gardens, Beaumond Heights, Humbergate, J...                      9   
Alderwood, Long Branch                                                  9   
Bathurst Manor, Downsview North, Wilson Heights                        19   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      23   
Berczy Park                                                            50   
Birch Cliff, Cliffside West                                             4   
Bloordale Gardens, Eringate, Markland Wood, Old...                      8   
Brockton, Exhibition Place, Parkdale Village                           23   
Business Reply Mail Processing Centre 969 Eastern                      16   
CFB Toronto, Downsview East                                             3   
CN Tower, Bathurst Quay, Island airport, Harbou...                     16   
Cabbagetown, St. James Town                                            46   
Caledonia-Fairbanks                                                     5   
Canada Post Gateway Processing Centre                                  11   
Cedarbrae                                                               8   
Central Bay Street                                                     50   
Chinatown, Grange Park, Kensington Market                              50   
Christie                                                               16   
Church and Wellesley                                                   50   
Clairlea, Golden Mile, Oakridge                                         9   
Clarks Corners, Sullivan, Tam O'Shanter                                10   
Cliffcrest, Cliffside, Scarborough Village West                         2   
Cloverdale, Islington, Martin Grove, Princess G...                      2   
Commerce Court, Victoria Hotel                                         50   
Davisville                                                             34   
Davisville North                                                       10   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                     15   
Del Ray, Keelesdale, Mount Dennis, Silverthorn                          4   
Design Exchange, Toronto Dominion Centre                               50   
Don Mills North                                                         6   
Dorset Park, Scarborough Town Centre, Wexford H...                      6   
Dovercourt Village, Dufferin                                           14   
Downsview Central                                                       3   
Downsview Northwest                                                     5   
Downsview West                                                          6   
Downsview, North Park, Upwood Park                                      4   
East Birchmount Park, Ionview, Kennedy Park                             4   
East Toronto                                                            5   
Emery, Humberlea                                                        2   
Fairview, Henry Farm, Oriole                                           50   
First Canadian Place, Underground city                                 50   
Flemingdon Park, Don Mills South                                       21   
Forest Hill North, Forest Hill West                                     4   
Glencairn                                                               5   
Guildwood, Morningside, West Hill                                       7   
Harbord, University of Toronto                                         33   
Harbourfront East, Toronto Islands, Union Statio

## Analyzing  neighborhoods

In [48]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot.head()

Accessories Store  Airport  Airport Food Court  Airport Gate  \
0                  0        0                   0             0   
1                  0        0                   0             0   
2                  0        0                   0             0   
3                  0        0                   0             0   
4                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                   0              0          0           0           0   
1                   0              0          0           0           0   
2                   0              0          0           0           0   
3                   0              0          0           0           0   
4                   0              0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Bike Shop  Bistro  \
0                   0      0         0           0          0       0   
1                   0      0         0           0          0       0   
2                   0      0         0           0          0       0   
3                   0      0         0           0          0       0   
4                   0      0         0           0          0       0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewery  Bridal Shop  Bubble Tea Shop  Building  Burger Joint  \
0        0            0                0         0             0   
1        0            0                0         0             0   
2        0            0                0         0             0   
3        0            0                0         0             0   
4        0            0                0         0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0              0         0            0         0                 0        0   
1              0         0            0         0                 0        0   
2              0         0            0         0                 0        0   
3              0         0            0         0                 0        0   
4              0   

In [66]:
toronto_onehot.shape

(1686, 256)

In [67]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Accessories Store  \
0                            Adelaide, King, Richmond           0.000000   
1                                           Agincourt           0.000000   
2   Agincourt North, L'Amoreaux East, Milliken, St...           0.000000   
3   Albion Gardens, Beaumond Heights, Humbergate, ...           0.000000   
4                              Alderwood, Long Branch           0.000000   
5     Bathurst Manor, Downsview North, Wilson Heights           0.000000   
6                                     Bayview Village           0.000000   
7                   Bedford Park, Lawrence Manor East           0.000000   
8                                         Berczy Park           0.000000   
9                         Birch Cliff, Cliffside West           0.000000   
10  Bloordale Gardens, Eringate, Markland Wood, Ol...           0.000000   
11       Brockton, Exhibition Place, Parkdale Village           0.000000   
12  Business Reply Mail Processing Centre 969 Eastern           0.000000   
13                        CFB Toronto, Downsview East           0.000000   
14  CN Tower, Bathurst Quay, Island airport, Harbo...           0.000000   
15                        Cabbagetown, St. James Town           0.000000   
16                                Caledonia-Fairbanks           0.000000   
17              Canada Post Gateway Processing Centre           0.000000   
18                                          Cedarbrae           0.000000   
19                                 Central Bay Street           0.000000   
20          Chinatown, Grange Park, Kensington Market           0.000000   
21                                           Christie           0.000000   
22                               Church and Wellesley           0.000000   
23                    Clairlea, Golden Mile, Oakridge           0.000000   
24            Clarks Corners, Sullivan, Tam O'Shanter           0.000000   
25    Cliffcrest, Cliffside, Scarborough Village West           0.000000   
26  Cloverdale, Islington, Martin Grove, Princess ...           0.000000   
27                     Commerce Court, Victoria Hotel           0.000000   
28                                         Davisville           0.000000   
29                                   Davisville North           0.000000   
30  Deer Park, Forest Hill SE, Rathnelly, South Hi...           0.000000   
31     Del Ray, Keelesdale, Mount Dennis, Silverthorn           0.000000   
32           Design Exchange, Toronto Dominion Centre           0.000000   
33                                    Don Mills North           0.000000   
34  Dorset Park, Scarborough Town Centre, Wexford ...           0.000000   
35                       Dovercourt Village, Dufferin           0.000000   
36                                  Downsview Central           0.000000   
37                                Downsview Northwest           0.000000   
38                                     Downsview West           0.000000   
39                 Downsview, North Park, Upwood Park           0.000000   
40        East Birchmount Park, Ionview, Kennedy Park           0.000000   
41                                       East Toronto           0.000000   
42                                   Emery, Humberlea           0.000000   
43                       Fairview, Henry Farm, Oriole           0.000000   
44             First Canadian Place, Underground city           0.000000   
45                   Flemingdon Park, Don Mills South           0.000000   
46                Forest Hill North, Forest Hill West           0.000000   
47                                          Glencairn           0.000000   
48                  Guildwood, Morningside, West Hill           0.000000   
49                     Harbord, University of Toronto           0.000000   
50  Harbourfront East, Toronto Islands, Union Station           0.000000   
51                          Harbourfront, Regent Park           0.000000   
52           

In [68]:
toronto_grouped.shape

(100, 256)

In [69]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide, King, Richmond----
                 venue  freq
0          Coffee Shop  0.08
1                 Café  0.06
2  American Restaurant  0.06
3           Steakhouse  0.06
4                Hotel  0.04


----Agincourt----
                       venue  freq
0             Breakfast Spot  0.25
1                     Lounge  0.25
2             Clothing Store  0.25
3               Skating Rink  0.25
4  Middle Eastern Restaurant  0.00


----Agincourt North, L'Amoreaux East, Milliken, Steeles East----
                       venue  freq
0                 Playground   0.5
1                       Park   0.5
2          Accessories Store   0.0
3  Middle Eastern Restaurant   0.0
4                      Motel   0.0


----Albion Gardens, Beaumond Heights, Humbergate, Jamestown, Mount Olive, Silverstone, South Steeles, Thistletown----
                  venue  freq
0         Grocery Store  0.22
1           Pizza Place  0.11
2           Coffee Shop  0.11
3  Fast Food Restaurant  0.11
4   Fried Chicke

### Putting information into a Pandas dataframe

In [72]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [74]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Adelaide, King, Richmond           Coffee Shop   
1                                          Agincourt                Lounge   
2  Agincourt North, L'Amoreaux East, Milliken, St...                  Park   
3  Albion Gardens, Beaumond Heights, Humbergate, ...         Grocery Store   
4                             Alderwood, Long Branch           Pizza Place   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0            Steakhouse                  Café   American Restaurant   
1        Breakfast Spot        Clothing Store          Skating Rink   
2            Playground           Yoga Studio              Dive Bar   
3              Pharmacy           Coffee Shop           Pizza Place   
4          Dance Studio                   Gym           Coffee Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0      Asian Restaurant             Gastropub                 Hotel   
1           Yoga Studio               Dog Run    Dim Sum Restaurant   
2      Department Store          Dessert Shop    Dim Sum Restaurant   
3   Fried Chicken Joint        Sandwich Place  Fast Food Restaurant   
4              Pharmacy          Skating Rink        Sandwich Place   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0           Pizza Place                   Bar          Burrito Place  
1                 Diner        Discount Store               Dive Bar  
2                 Diner        Discount Store              Drugstore  
3            Beer Store        Discount Store           Dessert Shop  
4                   Pub    Dim Sum Restaurant          Deli / Bodega

### Clustering Neighborhoods

In [75]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 1, 3, 3, 0, 0, 0, 0, 0], dtype=int32)

In [76]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() 

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1                     KFC       43.754387       -79.333021   
2           Variety Store       43.751974       -79.333114   
3  Victoria Village Arena       43.723481       -79.315635   
4             Tim Hortons       43.725517       -79.313103   

         Venue Category  Cluster Labels 1st Most Common Venue  \
0                  Park               3                  Park   
1  Fast Food Restaurant               3                  Park   
2     Food & Drink Shop               3                  Park   
3          Hockey Arena               0          Intersection   
4           Coffee Shop               0          Intersection   

  2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0  Fast Food Restaurant     Food & Drink Shop            Yoga Studio   
1  Fast Food Restaurant     Food & Drink Shop            Yoga Studio   
2  Fast Food Restaurant     Food & Drink Shop            Yoga Studio   
3          Hockey Arena           Coffee Shop  Portuguese Restaurant   
4          Hockey Arena           Coffee Shop  Portuguese Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0              Dive Bar          Dessert Shop    Dim Sum Restaurant   
1              Dive Bar          Dessert Shop    Dim Sum Restaurant   
2              Dive Bar          Dessert Shop    Dim Sum Restaurant   
3      Department Store          Dessert Shop    Dim Sum Restaurant   
4      Department Store          Dessert Shop    Dim Sum Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                 Diner        Discount Store              Drugstore  
1                 Diner        Discount Store              Drugstore  
2                 Diner        Discount Store              Drugstore  
3                 Diner        Discount Store               Dive Bar  
4                 Diner        Discount Store               Dive Bar

In [86]:
# create map
map_clusters = folium.Map(location=[latitude_toronto, longitude_toronto], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examining clusters

### Cluster 1

In [87]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0,toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude                 Venue Category  \
3                 43.725882       -79.315635                   Hockey Arena   
4                 43.725882       -79.313103                    Coffee Shop   
5                 43.725882       -79.312785          Portuguese Restaurant   
6                 43.725882       -79.313620                   Intersection   
7                 43.654260       -79.362017                         Bakery   
8                 43.654260       -79.361809                    Coffee Shop   
9                 43.654260       -79.357947           Gym / Fitness Center   
10                43.654260       -79.359874                            Spa   
11                43.654260       -79.361149                 Breakfast Spot   
12                43.654260       -79.356980                     Restaurant   
13                43.654260       -79.364503                 Breakfast Spot   
14                43.654260       -79.358967                            Pub   
15                43.654260       -79.356211                           Park   
16                43.654260       -79.359323                  Historic Site   
17                43.654260       -79.358127                 Chocolate Shop   
18                43.654260       -79.361832                 Farmers Market   
19                43.654260       -79.359515                    Coffee Shop   
20                43.654260       -79.365609                    Coffee Shop   
21                43.654260       -79.361442                    Coffee Shop   
22                43.654260       -79.360723                   Dessert Shop   
23                43.654260       -79.364329                    Coffee Shop   
24                43.654260       -79.357593          Performing Arts Venue   
25                43.654260       -79.359539                         Bakery   
26                43.654260       -79.354806                           Park   
27                43.654260       -79.358920             Mexican Restaurant   
28                43.654260       -79.357843              French Restaurant   
29                43.654260       -79.365657             Mexican Restaurant   
30                43.654260       -79.362195                           Park   
31                43.654260       -79.356503                           Café   
32                43.654260       -79.358709                         Bakery   
33                43.654260       -79.357078                    Coffee Shop   
34                43.654260       -79.358849                           Café   
35                43.654260       -79.358489                            Pub   
36                43.654260       -79.359436                     Shoe Store   
37                43.654260       -79.365873                    Event Space   
38                43.654260       -79.360440                 Ice Cream Shop   
39                43.654260       -79.359431             Italian Restaurant   
40                43.654260       -79.361005                 Cosmetics Shop   
41                43.654260       -79.357615                        Theater   
42                43.654260       -79.361222                    Art Gallery   
43                43.654260       -79.358862                           Café   
44                43.654260       -79.360073                        Brewery   
45                43.654260       -79.359667              Electronics Store   
46                43.654260       -79.356336                           Bank   
47                43.654260       -79.357463                     Beer Store   
48                43.654260       -79.358970                    Coffee Shop   
49                43.654260       -79.357119              Health Food Store   
50                43.654260       -79.356240                    Coffee Shop   
51                43.654260       -79.357538                   Antique Shop   
52                43.718518       -79.466776            

### Cluster 2

In [90]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude        Venue Category  \
336               43.689026       -79.456326  Fast Food Restaurant   
337               43.689026       -79.456300                  Park   
338               43.689026       -79.456333         Women's Store   
339               43.689026       -79.456317                Market   
340               43.689026       -79.448924                  Park   
1061              43.706876       -79.515869                  Park   
1368              43.815252       -79.289773                  Park   
1369              43.815252       -79.289867            Playground   
1437              43.679563       -79.380091              Building   
1438              43.679563       -79.378934            Playground   
1439              43.679563       -79.373788                  Park   
1440              43.679563       -79.382773                  Park   
1441              43.679563       -79.373842                 Trail   
1600              43.653654       -79.508145                  Park   
1601              43.653654       -79.501702                 River   

      Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
336                1                  Park         Women's Store   
337                1                  Park         Women's Store   
338                1                  Park         Women's Store   
339                1                  Park         Women's Store   
340                1                  Park         Women's Store   
1061               1                  Park           Yoga Studio   
1368               1                  Park            Playground   
1369               1                  Park            Playground   
1437               1                  Park                 Trail   
1438               1                  Park                 Trail   
1439               1                  Park                 Trail   
1440               1                  Park                 Trail   
1441               1                  Park                 Trail   
1600               1                  Park                 River   
1601               1                  Park                 River   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
336                 Market  Fast Food Restaurant           Yoga Studio   
337                 Market  Fast Food Restaurant           Yoga Studio   
338                 Market  Fast Food Restaurant           Yoga Studio   
339                 Market  Fast Food Restaurant           Yoga Studio   
340                 Market  Fast Food Restaurant           Yoga Studio   
1061         Deli / Bodega  Ethiopian Restaurant   Empanada Restaurant   
1368           Yoga Studio              Dive Bar      Department Store   
1369           Yoga Studio              Dive Bar      Department Store   
1437            Playground              Building      Department Store   
1438            Playground              Building      Department Store   
1439            Playground              Building      Department Store   
1440            Playground              Building      Department Store   
1441            Playground              Building      Department Store   
1600           Yoga Studio              Dive Bar      Department Store   
1601           Yoga Studio              Dive Bar      Department Store   

     6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
336                Dog Run           Dim Sum Restaurant                 Diner   
337                Dog Run           Dim Sum Restaurant                 Diner   
338                Dog Run           Dim Sum Restaurant                 Diner   
339                Dog Run           Dim Sum Restaurant                 Diner   
340                Dog Run           Dim Sum Restaurant                 Diner   
1061     Electronics Store  Eastern European Restaurant   Dumpling Restaurant   
1368          Dessert Shop           Dim Sum

### Cluster 3

In [91]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude Venue Category  Cluster Labels  \
852               43.75749       -79.370649      Cafeteria               2   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
852             Cafeteria           Yoga Studio           College Gym   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
852  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   

           7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
852  Eastern European Restaurant   Dumpling Restaurant             Drugstore   

    10th Most Common Venue  
852                Dog Run

### Cluster 4

In [92]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude              Venue Category  \
0                 43.753259       -79.332140                        Park   
1                 43.753259       -79.333021        Fast Food Restaurant   
2                 43.753259       -79.333114           Food & Drink Shop   
110               43.706397       -79.312913                   Gastropub   
111               43.706397       -79.309279        Gym / Fitness Center   
112               43.706397       -79.312410                    Pharmacy   
113               43.706397       -79.312270                        Bank   
114               43.706397       -79.313130                 Pizza Place   
115               43.706397       -79.308838        Fast Food Restaurant   
116               43.706397       -79.311783                        Café   
117               43.706397       -79.312196                   Pet Store   
118               43.706397       -79.313274                Intersection   
119               43.706397       -79.313957                 Pizza Place   
120               43.706397       -79.314105        Fast Food Restaurant   
121               43.706397       -79.313411          Athletics & Sports   
172               43.709577       -79.443930         Japanese Restaurant   
173               43.709577       -79.442378                         Pub   
174               43.709577       -79.444053            Sushi Restaurant   
175               43.709577       -79.443141                 Pizza Place   
176               43.709577       -79.442482                        Park   
177               43.650943       -79.549748                        Bank   
178               43.650943       -79.556107                 Golf Course   
202               43.695344       -79.315397                Skating Rink   
203               43.695344       -79.313658                 Curling Ice   
204               43.695344       -79.316759                  Beer Store   
205               43.695344       -79.318939                    Pharmacy   
206               43.695344       -79.314303                        Park   
207               43.695344       -79.317385                Dance Studio   
208               43.695344       -79.317577                    Bus Stop   
209               43.695344       -79.319287              Cosmetics Shop   
210               43.695344       -79.315145          Athletics & Sports   
211               43.695344       -79.315937                 Video Store   
266               43.643515       -79.576592                Liquor Store   
267               43.643515       -79.576600                 Coffee Shop   
268               43.643515       -79.576925                  Beer Store   
269               43.643515       -79.576721                        Café   
270               43.643515       -79.576924                    Pharmacy   
271               43.643515       -79.576556                 Pizza Place   
272               43.643515       -79.576370           Convenience Store   
273               43.643515       -79.577050                   Pet Store   
429               43.669542       -79.420485               Grocery Store   
430               43.669542       -79.426105                        Café   
431               43.669542       -79.426148          Italian Restaurant   
432               43.669542       -79.421366                 Coffee Shop   
433               43.669542       -79.426541                       Diner   
434               43.669542       -79.428054                  Restaurant   
435               43.669542       -79.419938                        Café   
436               43.669542       -79.419297                        Café   
437               43.669542       -79.421102               Grocery Store   
438               43.669542       -79.420499                  Baby Store   
439               43.669542       -79.426611                   Nightclub   
440               43.669542       -79.418106          

### Cluster 5

In [93]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude        Venue Category  \
103              43.806686       -79.199056  Fast Food Restaurant   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
103               4  Fast Food Restaurant           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
103    Falafel Restaurant  Ethiopian Restaurant   Empanada Restaurant   

    6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
103     Electronics Store  Eastern European Restaurant   Dumpling Restaurant   

    9th Most Common Venue 10th Most Common Venue  
103             Drugstore                Dog Run